# Proposition 1: Top 10 Regular Customer's Purchase Recurrence History
Retrieve a list of orders from the `Sales.Orders` table for the top 10 customers who have placed the most orders. For each order, calculate the difference in days (`diff`) between the current order's date and the date of the previous order made by the same customer. Sort the list of orders by `CustomerID`, `OrderDate`, and `OrderID`.
### Key Objectives:
1. **Identify Top Customers**: The query selects the top 10 customers based on the total number of orders they have placed.
2. **Retrieve Orders and Calculate Day Difference**: For each order by these customers, the query calculates the number of days between that order and the most recent prior order (if available).
3. **Sort the Results**: The result set is ordered by customer ID, order date, and order ID.
## Functional Specification
### Inputs
- **Sales.Orders table**: Contains order records, including `CustomerID`, `OrderDate`, and `OrderID`.
- **Sales.Customers table**: Contains customer records, including `CustomerID`.
### Outputs
- **CustomerID**: ID of the customer who placed the order.
- **OrderDate**: Date when the order was placed.
- **OrderID**: Unique identifier for each order.
- **diff**: The difference in days between the current order and the previous order by the same customer. If no previous order exists, `diff` will be `NULL`.
### Query Breakdown
1. **Top 10 Customers**:
    
    - The subquery selects the top 10 customers with the highest number of orders, using the `Sales.Customers` and `Sales.Orders` tables. It counts orders for each customer and orders the result in descending order of total orders.
    - The `TOP (10)` clause is used to limit the results to the top 10 customers.
2. **Order Details**:
    
    - For each order placed by one of the top 10 customers, the query retrieves the `CustomerID`, `OrderDate`, and `OrderID` from `Sales.Orders`.
3. **Date Difference Calculation**:
    
    - The `datediff` function is used to calculate the difference in days between the current order and the most recent previous order for the same customer.
    - The subquery finds the previous order by looking for the maximum order date that is less than or equal to the current order's date. If there are multiple orders on the same date, the one with the smaller `OrderID` is selected.
4. **Ordering**:
    
- The results are ordered by `CustomerID`, `OrderDate`, and `OrderID` to display the orders in a chronological manner for each customer.
### Edge Cases
- **No Previous Orders**: If a customer’s order is the first one, the `diff` value will be `NULL` as no prior order exists for comparison.
- **Same-Day Orders**: When multiple orders are placed by the same customer on the same day, the subquery ensures the previous order is selected based on the `OrderID`.
### Performance Considerations
- **Indexes**: Ensure indexes on `CustomerID`, `OrderDate`, and `OrderID` for both the `Sales.Orders` and `Sales.Customers` tables to optimize query performance.
- **Large Datasets**: If the dataset is large, consider pagination or limiting the number of orders returned per customer.

In [1]:
SELECT O1.CustomerID
,      O1.OrderDate
,      O1.OrderID
,      datediff(DD
               ,(SELECT TOP (1) O2.OrderDate
                 FROM Sales.Orders AS O2
                 WHERE O2.CustomerID = O1.CustomerID
                 AND (O2.OrderDate = O1.OrderDate AND O2.OrderID < O1.OrderID
                      OR O2.OrderDate < O1.OrderDate)
                 ORDER BY O2.OrderDate DESC, O2.OrderID DESC)
               ,O1.OrderDate) AS diff
FROM Sales.Orders AS O1
WHERE O1.CustomerID IN (
     SELECT TOP (10) C.CustomerID
     FROM Sales.Customers AS C
          INNER JOIN Sales.Orders AS O
               ON C.CustomerID = O.CustomerID
     GROUP BY C.CustomerID
     ORDER BY COUNT(O.OrderID) DESC
)
ORDER BY O1.CustomerID, O1.OrderDate, O1.OrderID;

(1445 rows affected)

Total execution time: 00:00:00.203

CustomerID OrderDate OrderID diff 70 2013-01-19 1063 NULL 70 2013-01-19 1065 0 70 2013-02-12 2132 24 70 2013-03-04 2961 20 70 2013-03-04 2967 0 70 2013-03-04 3014 0 70 2013-03-11 3402 7 70 2013-03-13 3571 2 70 2013-03-14 3658 1 70 2013-03-14 3659 0 70 2013-03-14 3680 0 70 2013-03-20 3990 6 70 2013-03-27 4330 7 70 2013-04-02 4603 6 70 2013-04-10 5012 8 70 2013-04-22 5731 12 70 2013-04-30 6164 8 70 2013-05-01 6199 1 70 2013-05-16 7106 15 70 2013-05-18 7243 2 70 2013-05-25 7609 7 70 2013-06-10 8489 16 70 2013-06-29 9658 19 70 2013-06-29 9665 0 70 2013-08-08 11974 40 70 2013-08-21 12551 13 70 2013-08-28 12869 7 70 2013-09-05 13338 8 70 2013-09-10 13596 5 70 2013-09-16 13813 6 70 2013-09-16 13898 0 70 2013-10-14 15329 28 70 2013-10-22 15726 8 70 2013-11-20 17279 29 70 2013-11-20 17350 0 70 2013-11-30 17863 10 70 2013-12-09 18325 9 70 2013-12-20 18870 11 70 2014-01-10 19974 21 70 2014-01-15 20177 5 70 2014-02-05 21370 21 70 2014-02-06 21462 1 70 2014-02-11 21738 5 70 2014-02-11 21761 0 70 2014-03-12 23351 29 70 2014-03-13 23467 1 70 2014-03-17 23599 4 70 2014-03-19 23729 2 70 2014-04-18 25394 30 70 2014-05-08 26578 20 70 2014-05-08 26598 0 70 2014-05-28 27697 20 70 2014-05-30 27909 2 70 2014-05-30 27927 0 70 2014-06-07 28493 8 70 2014-06-23 29430 16 70 2014-06-26 29718 3 70 2014-07-04 30154 8 70 2014-07-04 30207 0 70 2014-07-15 30857 11 70 2014-07-26 31611 11 70 2014-07-30 31823 4 70 2014-07-30 31850 0 70 2014-08-01 31901 2 70 2014-08-13 32607 12 70 2014-08-27 33325 14 70 2014-08-28 33390 1 70 2014-09-04 33795 7 70 2014-09-10 34022 6 70 2014-09-12 34203 2 70 2014-09-15 34328 3 70 2014-09-15 34340 0 70 2014-09-16 34371 1 70 2014-09-16 34384 0 70 2014-09-24 34773 8 70 2014-09-24 34801 0 70 2014-09-25 34853 1 70 2014-10-10 35752 15 70 2014-10-11 35815 1 70 2014-10-13 35888 2 70 2014-10-14 35909 1 70 2014-10-16 36102 2 70 2014-11-13 37868 28 70 2014-12-17 39668 34 70 2014-12-24 40157 7 70 2014-12-30 40527 6 70 2015-01-01 40701 2 70 2015-01-06 40958 5 70 2015-01-24 41986 18 70 2015-01-24 41996 0 70 2015-02-13 43234 20 70 2015-03-02 44217 17 70 2015-03-09 44641 7 70 2015-03-12 44925 3 70 2015-03-26 45774 14 70 2015-03-30 45985 4 70 2015-03-31 46089 1 70 2015-04-06 46444 6 70 2015-04-09 46680 3 70 2015-04-09 46725 0 70 2015-04-13 46921 4 70 2015-04-13 46925 0 70 2015-04-14 47028 1 70 2015-04-14 47051 0 70 2015-04-23 47688 9 70 2015-04-28 47952 5 70 2015-04-29 48017 1 70 2015-04-30 48130 1 70 2015-04-30 48194 0 70 2015-05-05 48465 5 70 2015-05-15 49077 10 70 2015-05-19 49305 4 70 2015-05-27 49855 8 70 2015-05-29 50046 2 70 2015-06-23 51625 25 70 2015-06-29 52003 6 70 2015-07-09 52763 10 70 2015-07-09 52790 0 70 2015-07-22 53684 13 70 2015-07-22 53697 0 70 2015-07-24 53887 2 70 2015-08-12 55068 19 70 2015-08-12 55088 0 70 2015-08-18 55378 6 70 2015-08-21 55568 3 70 2015-08-27 55908 6 70 2015-09-04 56385 8 70 2015-09-22 57581 18 70 2015-09-23 57733 1 70 2015-09-23 57780 0 70 2015-11-18 61225 56 70 2016-01-07 64457 50 70 2016-01-13 64852 6 70 2016-01-22 65390 9 70 2016-01-26 65665 4 70 2016-01-26 65681 0 70 2016-02-01 65922 6 70 2016-02-10 66408 9 70 2016-02-17 66804 7 70 2016-02-17 66829 0 70 2016-03-08 68095 20 70 2016-03-11 68309 3 70 2016-04-30 71515 50 70 2016-05-18 72704 18 90 2013-01-29 1455 NULL 90 2013-02-06 1890 8 90 2013-02-25 2648 19 90 2013-03-01 2865 4 90 2013-03-01 2878 0 90 2013-03-08 3248 7 90 2013-03-12 3455 4 90 2013-03-12 3521 0 90 2013-03-19 3881 7 90 2013-03-19 3926 0 90 2013-04-02 4626 14 90 2013-04-22 5693 20 90 2013-04-22 5757 0 90 2013-05-08 6638 16 90 2013-05-16 7139 8 90 2013-05-30 7854 14 90 2013-07-18 10807 49 90 2013-07-22 10965 4 90 2013-08-10 12044 19 90 2013-08-20 12470 10 90 2013-08-27 12849 7 90 2013-08-29 12963 2 90 2013-09-04 13249 6 90 2013-09-16 13864 12 90 2013-10-16 15460 30 90 2013-10-16 15470 0 90 2013-10-16 15493 0 90 2013-10-17 15515 1 90 2013-11-08 16678 22 90 2013-11-15 17032 7 90 2013-11-15 17059 0 90 2013-11-25 17546 10 90 2013-12-04 18096 9 90 2013-12-09 18358 5 90 2013-12-10 18381 1 90 2013-1

# Proposition 2: Salesperson of the Year
Retrieve <span style="color: var(--vscode-foreground);">a list of salespeople, along with the total number of sales they made in the most recent year of orders. The query retrieves the salesperson details from the </span> `Application.People` <span style="color: var(--vscode-foreground);">table and matches them with sales data from the </span> `Sales.Orders` <span style="color: var(--vscode-foreground);">table, displaying sales in descending order of the number of sales made.</span>
### Key Objectives:
1. **Filter Orders for the Most Recent Year**: The query identifies the most recent year for which sales data exists and counts the number of sales made by each salesperson during that year.
2. **Join Sales Data with Person Details**: Salespeople details from the `Application.People` table are combined with their sales counts.
3. **Order by Sales and Person ID**: The result is ordered by the number of sales in descending order, followed by `PersonID` to break any ties.
## Functional Specification
### Inputs
- **Sales.Orders table**: Contains order records, including `SalespersonPersonID` and `OrderDate`.
- **Application.People table**: Contains personal details of individuals, including `PersonID`, `FullName`, and `IsSalesperson`.
### Outputs
- **PersonID**: The unique identifier for the salesperson.
- **FullName**: The full name of the salesperson.
- **TotalSalesMade**: The total number of sales made by the salesperson during the most recent year of sales data.
### Query Breakdown
1. **Temporary Table for Sales Data (`EmpSales`)**:
    
    - The `EmpSales` common table expression (CTE) is used to gather sales data for each salesperson during the most recent year.
    - The `WHERE` clause filters orders based on the year of the most recent order date in the `Sales.Orders` table, determined by a subquery using `MAX(OrderDate)`.
    - The query counts the number of orders (`TotalSalesMade`) made by each salesperson and groups them by `SalespersonPersonID`.
2. **Joining Sales Data with People Information**:
    
    - The main query selects people from the `Application.People` table, where the `IsSalesperson` flag is set to 1 (indicating the person is a salesperson).
    - A `LEFT OUTER JOIN` is performed between `Application.People` and the `EmpSales` CTE to match sales data with each person based on `PersonID`. This ensures that even salespeople who made no sales in the most recent year are included in the final result.
3. **Sorting**:
    
- The result is ordered by `TotalSalesMade` in descending order, ensuring that the salespeople with the highest number of sales appear first. If two salespeople have the same number of sales, they are further sorted by their `PersonID`.
### Edge Cases
- **No Sales in the Most Recent Year**: If no sales were made by a salesperson in the most recent year, the `TotalSalesMade` column will be `NULL`.
- **Salespeople with No Sales**: Salespeople who did not make any sales in the most recent year will still appear in the result set due to the `LEFT OUTER JOIN`.
- **Multiple Sales in a Day**: If a salesperson made multiple sales on the same day, they are all counted in `TotalSalesMade`.
### Assumptions
- The `Sales.Orders` table includes a `SalespersonPersonID` for each order, and the `OrderDate` is properly formatted and indexed.
- Only the most recent year's sales are relevant for this query.
- The `Application.People` table includes an `IsSalesperson` flag to filter the people who are salespeople.

In [2]:
WITH EmpSales AS
(
    SELECT SalespersonPersonID, COUNT(SalespersonPersonID) AS TotalSalesMade
    FROM Sales.Orders
    WHERE YEAR(OrderDate) = (
        SELECT YEAR(MAX(OrderDate))
        FROM Sales.Orders
    )
    GROUP BY SalespersonPersonID
)
SELECT P.PersonID, P.FullName, ES.TotalSalesMade
FROM Application.People AS P
    LEFT OUTER JOIN EmpSales AS ES
        ON ES.SalespersonPersonID = P.PersonID
WHERE P.IsSalesperson = 1
ORDER BY TotalSalesMade DESC, P.PersonID;


(10 rows affected)

Total execution time: 00:00:00.031

PersonID FullName TotalSalesMade 15 Taj Shand 1001 16 Archer Lamble 999 13 Hudson Hollinworth 993 20 Jack Potter 992 3 Hudson Onslow 966 2 Kayla Woodcock 958 7 Amy Trefl 941 8 Anthony Grosse 939 14 Lily Code 921 6 Sophia Hinton 907

# Proposition 3: Discounted Sales Quantity
Retrieve the total quantity of items picked for orders that are eligible for special discounts. The eligible orders are those placed by customers belonging to a specific buying group during a specified discount period and include items from stock groups that are part of special deals.
### Key Objectives:
1. **Identify Special Discount Periods and Eligible Stock Items**: Extract information about discount periods and associated stock items.
2. **Filter Orders by Discount Eligibility**: Only include orders placed during the discount period by customers in specific buying groups.
3. **Calculate Total Picked Quantity**: For each eligible item, calculate the total quantity picked from the order lines.
## Functional Specification
### Inputs
- **Sales.SpecialDeals table**: Contains information about special discount periods, including `StartDate`, `EndDate`, `StockGroupID`, and `BuyingGroupID`.
- **Warehouse.StockItemStockGroups table**: Contains the mapping between stock items and their respective stock groups, including `StockItemID` and `StockGroupID`.
- **Sales.Orders table**: Contains order information, including `OrderID`, `CustomerID`, and `OrderDate`.
- **Sales.Customers table**: Contains customer information, including `CustomerID` and `BuyingGroupID`.
- **Sales.OrderLines table**: Contains details about order lines, including `OrderID`, `StockItemID`, and `PickedQuantity`.
### Outputs
- **StockItemID**: ID of the stock item included in the eligible orders.
- **TotalPickedQuantity**: The total quantity of each item that was picked for eligible orders.
### Query Breakdown
1. **Common Table Expressions (CTEs)**:
    
    - **DiscountInfo**: Extracts the `StartDate`, `EndDate`, `StockGroupID`, and `BuyingGroupID` for each special deal from the `Sales.SpecialDeals` table.
    - **DiscountedItems**: Retrieves the `StockItemID` of items that belong to stock groups participating in any special deal from the `Warehouse.StockItemStockGroups` table.
2. **Main Query**:
    
    - Joins the `Sales.Orders`, `Sales.Customers`, and `Sales.OrderLines` tables to filter the orders that meet the following conditions:
        - The customer belongs to a buying group that matches the special deal (`C.BuyingGroupID = DN.BuyingGroupID`).
        - The order was placed within the discount period (`O.OrderDate BETWEEN DN.StartDate AND DN.EndDate`).
        - The order includes items that are part of the discounted stock groups (`OL.StockItemID IN (DI.StockItemID)`).
    - Filters only those items for which a positive `PickedQuantity` is recorded (`OL.PickedQuantity > 0`).
    - Groups the results by `StockItemID` and calculates the total quantity picked for each eligible stock item (`SUM(OL.PickedQuantity)`).
3. **Ordering**:
    
- The result set is ordered by `StockItemID` to display the items in ascending order.
### Edge Cases
- **No Picked Quantity**: If an item has a `PickedQuantity` of 0 or less, it will be excluded from the results.
- **Overlapping Deals**: If multiple deals exist for the same `StockGroupID` or `BuyingGroupID` during overlapping periods, all qualifying orders during those periods will be considered.
- **No Special Deals**: If no active deals exist for the queried items or groups, the result will be empty.
### Assumptions
- Special deals are properly defined in the `Sales.SpecialDeals` table with relevant `StartDate`, `EndDate`, `StockGroupID`, and `BuyingGroupID`.
- The relationships between stock items and stock groups are accurately reflected in the `Warehouse.StockItemStockGroups` table.
- The query assumes that orders and their associated customers and order lines are correctly linked in the database.
- It is assumed that orders only placed within the discount period and by customers in the right buying group are to be included.

In [3]:
WITH DiscountInfo AS (
    SELECT StartDate, EndDate, StockGroupID, BuyingGroupID
    FROM Sales.SpecialDeals
),
DiscountedItems AS (
    SELECT StockItemID
    FROM Warehouse.StockItemStockGroups
    WHERE StockGroupID IN (
        SELECT StockGroupID
        FROM Sales.SpecialDeals
    )
)
SELECT OL.StockItemID, SUM(OL.PickedQuantity) AS TotalPickedQuantity
FROM DiscountInfo AS DN
    ,DiscountedItems AS DI
    ,Sales.Orders AS O
        INNER JOIN Sales.Customers AS C
            ON O.CustomerID = C.CustomerID
        INNER JOIN Sales.OrderLines AS OL
            ON O.OrderID = OL.OrderID
WHERE (C.BuyingGroupID = DN.BuyingGroupID) 
    AND (O.OrderDate BETWEEN DN.StartDate AND DN.EndDate)
    AND (OL.StockItemID IN (DI.StockItemID))
    AND (OL.PickedQuantity > 0)
GROUP BY OL.StockItemID
ORDER BY OL.StockItemID;

(14 rows affected)

Total execution time: 00:00:00.064

StockItemID TotalPickedQuantity 1 247 2 212 4 212 5 130 6 201 7 152 8 218 9 189 10 204 11 139 12 196 13 248 14 140 15 255

# Proposition 4: Non-Discounted Sales Quantity
Calculate the total quantity of items picked from orders containing discounted items for specific customer buying groups. The discounts are applied based on special deals that occur within a given date range. Aggregate the query based on the picked quantity for each discounted item and returns the total picked quantity, sorted by item ID.
### Key Objectives:
1. **Filter Special Deals**: Retrieve special deal information from `Sales.SpecialDeals` to identify the stock groups and buying groups that are eligible for discounts.
2. **Identify Discounted Items**: Get the stock items that belong to the stock groups associated with special deals.
3. **Calculate Picked Quantities**: For each order line that includes a discounted item, calculate the total picked quantity where orders belong to eligible customers, and the order date falls outside the relevant discount period.
4. **Aggregate Results**: Return the total picked quantity for each stock item, sorted by `StockItemID`.
## Functional Specification
### Inputs
- **Sales.SpecialDeals**: Contains special deal records, including start date, end date, stock group, and buying group.
- **Warehouse.StockItemStockGroups**: Maps stock items to stock groups, helping identify which items are part of a discounted stock group.
- **Sales.Customers**: Contains customer information, including their buying group.
- **Sales.Orders**: Stores order data, including order date and customer information.
- **Sales.OrderLines**: Stores detailed order line items, including stock item ID and picked quantity.
### Outputs
- **StockItemID**: The ID of the discounted stock item.
- **TotalPickedQuantity**: The total quantity of the item picked across all eligible orders.
### Query Breakdown
1. **CTE - DiscountInfo**:
    
    - The Common Table Expression (CTE) `DiscountInfo` selects the `StartDate`, `EndDate`, `StockGroupID`, and `BuyingGroupID` from `Sales.SpecialDeals`, representing the time period, stock groups, and buying groups involved in special discount deals.
2. **CTE - DiscountedItems**:
    
    - The `DiscountedItems` CTE retrieves the `StockItemID` from the `Warehouse.StockItemStockGroups` table where the stock group is involved in a special deal, based on the `StockGroupID` in `Sales.SpecialDeals`.
3. **Main Query**:
    
    - **Join Operations**:
        - The main query joins `Sales.Orders`, `Sales.Customers`, and `Sales.OrderLines` to filter the relevant orders and customers.
        - The query applies cross joins with `DiscountInfo` and `DiscountedItems` to access discount and item data.
    - **Filtering**:
        - The query checks whether the customer’s buying group (`C.BuyingGroupID`) matches the buying group in the discount (`DN.BuyingGroupID`).
        - It ensures that the order date falls outside of the special deal's time period. This is achieved using two conditions:
            1. Orders between the beginning of the year and the start date of the deal.
            2. Orders between the end date of the deal and the end of the year.
        - It filters out order lines that do not have discounted items (`OL.StockItemID IN (DI.StockItemID)`) or have zero picked quantities (`OL.PickedQuantity > 0`).
    - **Aggregation**:
        - The query groups by `OL.StockItemID` and calculates the total picked quantity (`SUM(OL.PickedQuantity)`) for each item.
    - **Sorting**:
        - The result is ordered by `StockItemID`.
### Edge Cases
- **No Picked Quantities**: If the picked quantity is 0, that order line will be excluded from the results.
- **Multiple Special Deals**: The query can handle customers and stock items that may be part of multiple special deals within the same or different date ranges.
- **Order Dates Outside Special Deal Periods**: Orders placed within the special deal periods will be filtered out, as they are not included for this calculation.
### Assumptions
- Each customer belongs to one buying group, and orders placed by that customer will always belong to that buying group.
- The special deals defined in the `Sales.SpecialDeals` table can span different time periods and apply to specific stock groups and buying groups.
- The necessary indexes on the `StockItemID`, `OrderDate`, and `CustomerID` fields are in place to optimize query performance.

In [4]:
WITH DiscountInfo AS (
    SELECT StartDate, EndDate, StockGroupID, BuyingGroupID
    FROM Sales.SpecialDeals
),
DiscountedItems AS (
    SELECT StockItemID
    FROM Warehouse.StockItemStockGroups
    WHERE StockGroupID IN (
        SELECT StockGroupID
        FROM Sales.SpecialDeals
    )
)
SELECT OL.StockItemID, SUM(OL.PickedQuantity) AS TotalPickedQuantity
FROM DiscountInfo AS DN
    ,DiscountedItems AS DI
    ,Sales.Orders AS O
        INNER JOIN Sales.Customers AS C
            ON O.CustomerID = C.CustomerID
        INNER JOIN Sales.OrderLines AS OL
            ON O.OrderID = OL.OrderID
WHERE (C.BuyingGroupID = DN.BuyingGroupID) 
    AND ((O.OrderDate BETWEEN DATEFROMPARTS(YEAR(DN.StartDate), 1, 1) AND DN.StartDate)
        OR (O.OrderDate BETWEEN DN.EndDate AND DATEFROMPARTS(YEAR(DN.EndDate), 12, 31)))
    AND (OL.StockItemID IN (DI.StockItemID))
    AND (OL.PickedQuantity > 0)
GROUP BY OL.StockItemID
ORDER BY OL.StockItemID;

(14 rows affected)

Total execution time: 00:00:00.032

StockItemID TotalPickedQuantity 1 213 2 249 4 269 5 289 6 159 7 165 8 255 9 205 10 175 11 243 12 295 13 205 14 263 15 201

# Proposition 5: Running Total Expected Expenses
Calculate the total expected expense for each finalized purchase order in the `Purchasing.PurchaseOrderLines` table, then compute a running total of these expenses, where each purchase order's expense is accumulated along with the previous orders. Order the result set by `PurchaseOrderID`.
### Key Objectives:
1. **Calculate Total Expense for Each Finalized Purchase Order**: The query sums the product of `ExpectedUnitPricePerOuter` and `OrderedOuters` for each finalized purchase order.
2. **Compute Running Total**: For each purchase order, the query computes a cumulative total of expenses, including the current order and all preceding orders.
3. **Order the Results**: The query results are sorted by `PurchaseOrderID` in ascending order.
## Functional Specification
### Inputs
- **Purchasing.PurchaseOrderLines table**: Contains purchase order details, including `PurchaseOrderID`, `ExpectedUnitPricePerOuter`, `OrderedOuters`, and `IsOrderLineFinalized`.
### Outputs
- **PurchaseOrderID**: Unique identifier of each finalized purchase order.
- **TotalExpense**: The total expected expense for each purchase order, calculated as the sum of `ExpectedUnitPricePerOuter * OrderedOuters`.
- **RunningExpense**: The cumulative total of expected expenses, calculated by summing the total expenses of all purchase orders with a `PurchaseOrderID` less than or equal to the current one.
### Query Breakdown
1. **Calculate Total Expected Expense (CTE)**:
    
    - A Common Table Expression (CTE) named `TotalExpectedExpense` is created. It calculates the total expected expense for each purchase order where `IsOrderLineFinalized = 1`, meaning the order line is finalized.
    - The total expected expense is calculated by multiplying `ExpectedUnitPricePerOuter` by `OrderedOuters` for each line, and then summing this value for all lines that belong to the same `PurchaseOrderID`.
    - The `GROUP BY PurchaseOrderID` clause is used to aggregate the expenses for each purchase order.
2. **Retrieve Total Expense and Running Expense**:
    
    - For each purchase order, the query retrieves the `PurchaseOrderID` and `TotalExpense` from the `TotalExpectedExpense` CTE.
    - The running total (`RunningExpense`) is calculated by summing the `TotalExpense` of the current purchase order and all preceding ones, based on the condition `TEE2.PurchaseOrderID <= TEE1.PurchaseOrderID`.
3. **Order Results**:
    
- The result set is ordered by `PurchaseOrderID` in ascending order, ensuring that the running total is calculated in a sequential manner.
### Edge Cases
- **No Finalized Order Lines**: If there are no finalized lines (`IsOrderLineFinalized = 0`), the query will return no rows, or potentially a `NULL` result set.
- **Single Purchase Order**: If there is only one purchase order in the table, the `RunningExpense` will be equal to `TotalExpense` for that single record.
### Assumptions
- The `Purchasing.PurchaseOrderLines` table contains valid and meaningful data for purchase order lines.
- The purchase orders are sequentially identified by `PurchaseOrderID`, and the running total is calculated in that sequential order.
- There are no significant performance concerns around the correlated subquery for the running total, though it could be optimized with window functions in some databases.
### Performance Considerations
- The query uses a correlated subquery to calculate the running total, which may not scale efficiently with large datasets. An alternative approach using window functions (like `SUM() OVER` in SQL Server) may offer better performance.

In [5]:
WITH TotalExpectedExpense AS (
    SELECT PurchaseOrderID, SUM(ExpectedUnitPricePerOuter * OrderedOuters) AS TotalExpense
    FROM Purchasing.PurchaseOrderLines
    WHERE IsOrderLineFinalized = 1
    GROUP BY PurchaseOrderID
)
SELECT 
    TEE1.PurchaseOrderID
,   TEE1.TotalExpense
,   (SELECT SUM(TEE2.TotalExpense)
     FROM TotalExpectedExpense AS TEE2
     WHERE TEE2.PurchaseOrderID <= TEE1.PurchaseOrderID) AS RunningExpense
FROM TotalExpectedExpense AS TEE1
ORDER BY TEE1.PurchaseOrderID;

(2072 rows affected)

Total execution time: 00:00:00.472

PurchaseOrderID TotalExpense RunningExpense 1 313.50 313.50 2 21732.00 22045.50 3 2740.50 24786.00 4 42481.20 67267.20 5 35067.50 102334.70 6 5528.50 107863.20 7 10000.50 117863.70 8 657.00 118520.70 9 9281.50 127802.20 10 1037.50 128839.70 11 19869.50 148709.20 12 6661.50 155370.70 13 261.00 155631.70 14 16279.45 171911.15 15 13325.00 185236.15 16 3768.00 189004.15 17 8808.00 197812.15 18 288.00 198100.15 19 5230.20 203330.35 20 7250.00 210580.35 21 5116.00 215696.35 22 157.50 215853.85 23 3639.55 219493.40 24 1245.00 220738.40 25 19278.00 240016.40 26 1436.00 241452.40 27 832.50 242284.90 28 2380.00 244664.90 29 1037.50 245702.40 30 2376.00 248078.40 31 10940.00 259018.40 32 168.00 259186.40 33 126.00 259312.40 34 10600.00 269912.40 35 8525.00 278437.40 36 1242.00 279679.40 37 144.00 279823.40 38 510.00 280333.40 39 2646.00 282979.40 40 553.50 283532.90 41 1110.00 284642.90 42 1530.00 286172.90 43 3648.00 289820.90 44 148.50 289969.40 45 170.00 290139.40 46 1150.00 291289.40 47 7494.00 298783.40 48 297.00 299080.40 49 1364.00 300444.40 50 6162.00 306606.40 51 7590.00 314196.40 52 9702.00 323898.40 53 144.00 324042.40 54 756.00 324798.40 55 139.50 324937.90 56 8382.00 333319.90 57 8850.00 342169.90 58 11514.00 353683.90 59 14358.00 368041.90 60 14358.00 382399.90 61 2448.00 384847.90 62 8815.00 393662.90 63 16410.00 410072.90 64 1020.00 411092.90 65 19830.00 430922.90 66 340.00 431262.90 67 20514.00 451776.90 68 22434.00 474210.90 69 25014.00 499224.90 70 2244.00 501468.90 71 26550.00 528018.90 72 26790.00 554808.90 73 26826.00 581634.90 74 26310.00 607944.90 75 26022.00 633966.90 76 3804.00 637770.90 77 29970.00 667740.90 78 31302.00 699042.90 79 33042.00 732084.90 80 1190.00 733274.90 81 36678.00 769952.90 82 2040.00 771992.90 83 36066.00 808058.90 84 1360.00 809418.90 85 1440.00 810858.90 86 37590.00 848448.90 87 2210.00 850658.90 88 37602.00 888260.90 89 2550.00 890810.90 90 38868.00 929678.90 91 3230.00 932908.90 92 37452.00 970360.90 93 2550.00 972910.90 94 37212.00 1010122.90 95 4080.00 1014202.90 96 2052.00 1016254.90 97 1700.00 1017954.90 98 36432.00 1054386.90 99 4420.00 1058806.90 100 36552.00 1095358.90 101 3740.00 1099098.90 102 36000.00 1135098.90 103 4420.00 1139518.90 104 36324.00 1175842.90 105 3740.00 1179582.90 106 38472.00 1218054.90 107 3910.00 1221964.90 108 2664.00 1224628.90 109 43866.00 1268494.90 110 4760.00 1273254.90 111 43848.00 1317102.90 112 4080.00 1321182.90 113 43740.00 1364922.90 114 4760.00 1369682.90 115 46392.00 1416074.90 116 4930.00 1421004.90 117 45744.00 1466748.90 118 5440.00 1472188.90 119 672.00 1472860.90 120 47754.00 1520614.90 121 5440.00 1526054.90 122 49662.00 1575716.90 123 4760.00 1580476.90 124 49566.00 1630042.90 125 6630.00 1636672.90 126 54282.00 1690954.90 127 5950.00 1696904.90 128 56208.00 1753112.90 129 5346.80 1758459.70 130 4524.00 1762983.70 131 59790.00 1822773.70 132 5100.00 1827873.70 133 62742.00 1890615.70 134 5259.20 1895874.90 135 64620.00 1960494.90 136 4809.60 1965304.50 137 67464.00 2032768.50 138 7765.60 2040534.10 139 70686.00 2111220.10 140 7650.40 2118870.50 141 170.00 2119040.50 142 70542.00 2189582.50 143 7590.00 2197172.50 144 70890.00 2268062.50 145 7063.60 2275126.10 146 71202.00 2346328.10 147 8522.40 2354850.50 148 71046.00 2425896.50 149 7688.80 2433585.30 150 69630.00 2503215.30 151 8599.20 2511814.50 152 2952.00 2514766.50 153 72426.00 2587192.50 154 9986.80 2597179.30 155 73110.00 2670289.30 156 10387.20 2680676.50 157 74460.00 2755136.50 158 10409.20 2765545.70 159 76524.00 2842069.70 160 11072.80 2853142.50 161 79524.00 2932666.50 162 12109.20 2944775.70 163 912.00 2945687.70 164 1020.00 2946707.70 165 81786.00 3028493.70 166 11462.00 3039955.70 167 84084.00 3124039.70 168 12158.40 3136198.10 169 85044.00 3221242.10 170 11401.60 3232643.70 171 85158.00 3317801.70 172 12312.00 3330113.70 173 88590.00 3418703.70 174 11785.60 3430489.30 175 2208.00 3432697.30 176 90474.00 3523171.30 177 10535.20 3533706.50 178 95376.00 3629082.50 179 11423.

# Proposition 6: List of Selected Customer's Ordered Items
Define a table-valued function `Sales.CustomerOrderItemsList` that retrieves a list of order items for a given customer, including the `StockItemID`, `PickedQuantity`, and `UnitPrice`. The main query should use this function in conjunction with the `CROSS APPLY` operator to retrieve and display a detailed list of customers along with the associated order items. The result is ordered by `CustomerID`.
### Key Objectives:
1. **Define a Table-Valued Function**: The function `Sales.CustomerOrderItemsList` is designed to return order line details (`StockItemID`, `PickedQuantity`, and `UnitPrice`) for a specified customer.
2. **Apply the Function to Each Customer**: The main query uses `CROSS APPLY` to retrieve the list of order items for each customer and display it alongside customer information.
3. **Sort Results by Customer ID**: The result set is ordered by `CustomerID` to group the orders and order items by customer.
## Functional Specification
### Inputs
1. **`Sales.Customers` table**: Contains customer records, including `CustomerID` and `CustomerName`.
2. **`Sales.Orders` table**: Contains order records, including `OrderID` and `CustomerID`.
3. **`Sales.OrderLines` table**: Contains order line records, including `OrderID`, `StockItemID`, `PickedQuantity`, and `UnitPrice`.
4. **Table-Valued Function Input**:
    - The function `Sales.CustomerOrderItemsList` takes a single parameter:
        - `@CustomerID` (INT): Represents the ID of the customer for which order items are to be retrieved.
### Outputs
1. **Customer Information**:
    
    - `CustomerID`: Unique identifier for each customer.
    - `CustomerName`: Name of the customer.
2. **Order Line Information**:
    
    - `StockItemID`: Identifier for the stock item.
    - `PickedQuantity`: Quantity of the item picked for the order.
    - `UnitPrice`: Price per unit of the stock item.
### Functionality
1. **Create or Alter Function**:
    
    - The `Sales.CustomerOrderItemsList` function retrieves the stock items, picked quantities, and unit prices for all order lines associated with a given customer.
    - The function joins the `Sales.Orders` table with `Sales.OrderLines` based on `OrderID` to fetch the order items associated with the orders of the specified customer (`@CustomerID`).
2. **Main Query**:
    
- The main query retrieves the `CustomerID` and `CustomerName` from `Sales.Customers`.
- For each customer, the `CROSS APPLY` operator is used to call the `Sales.CustomerOrderItemsList` function, which returns the order line details for that customer.
- The result is ordered by `CustomerID`.
### Query Breakdown
1. **Function Definition**:
    
    - The `Sales.CustomerOrderItemsList` function accepts a `CustomerID` as input and returns all order line details (`StockItemID`, `PickedQuantity`, and `UnitPrice`) for that customer.
    - The function uses an `INNER JOIN` between `Sales.Orders` and `Sales.OrderLines` based on the common `OrderID` key.
2. **Main Query**:
    
    - The main query retrieves each customer’s details (`CustomerID` and `CustomerName`) from the `Sales.Customers` table.
    - The `CROSS APPLY` operator is used to call the `Sales.CustomerOrderItemsList` function for each customer, which returns the stock items and order line details related to that customer.
    - The result set is ordered by `CustomerID`.
### Edge Cases
- **Customers with No Orders**: If a customer has no orders, the `CROSS APPLY` will not return any order items for that customer, and they will be excluded from the result set.
- **Customers with Multiple Orders**: The function will retrieve all order line items for each customer across multiple orders.
- **Performance Considerations**: If there are a large number of customers or orders, this query might benefit from appropriate indexing on `CustomerID` and `OrderID` to ensure performance is optimal.
### Assumptions
- The `Sales.Orders` and `Sales.OrderLines` tables have appropriate foreign keys linking them via `OrderID`.
- There is no requirement to include customers who have not placed any orders in the result set. Only customers with orders will be returned.
- The function is intended to handle typical scenarios where a customer has multiple orders and multiple items per order.

In [6]:
CREATE OR ALTER FUNCTION Sales.CustomerOrderItemsList
    (@CustomerID AS INT)
    RETURNS TABLE
AS
RETURN
    SELECT OL.StockItemID, OL.PickedQuantity, OL.UnitPrice
    FROM Sales.Orders AS O
        INNER JOIN Sales.OrderLines AS OL
            ON O.OrderID = OL.OrderID
    WHERE @CustomerID = O.CustomerID
GO

SELECT 
    C.CustomerID
,   C.CustomerName
,   COIL.StockItemID
,   COIL.PickedQuantity
,   COIL.UnitPrice
FROM Sales.Customers AS C
    CROSS APPLY Sales.CustomerOrderItemsList(C.CustomerID) AS COIL
ORDER BY C.CustomerID;

Commands completed successfully.

(231412 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:00:00.951

CustomerID CustomerName StockItemID PickedQuantity UnitPrice 1 Tailspin Toys (Head Office) 10 6 32.00 1 Tailspin Toys (Head Office) 214 7 90.00 1 Tailspin Toys (Head Office) 90 120 18.00 1 Tailspin Toys (Head Office) 74 4 285.00 1 Tailspin Toys (Head Office) 124 5 32.00 1 Tailspin Toys (Head Office) 124 7 32.00 1 Tailspin Toys (Head Office) 20 1 13.00 1 Tailspin Toys (Head Office) 2 7 25.00 1 Tailspin Toys (Head Office) 166 50 42.00 1 Tailspin Toys (Head Office) 47 9 13.00 1 Tailspin Toys (Head Office) 27 7 13.00 1 Tailspin Toys (Head Office) 157 10 30.00 1 Tailspin Toys (Head Office) 198 48 4.10 1 Tailspin Toys (Head Office) 16 8 13.00 1 Tailspin Toys (Head Office) 168 10 29.00 1 Tailspin Toys (Head Office) 194 72 4.10 1 Tailspin Toys (Head Office) 180 25 1.11 1 Tailspin Toys (Head Office) 180 25 1.11 1 Tailspin Toys (Head Office) 199 240 3.70 1 Tailspin Toys (Head Office) 157 10 30.00 1 Tailspin Toys (Head Office) 72 6 230.00 1 Tailspin Toys (Head Office) 93 36 18.00 1 Tailspin Toys (Head Office) 160 60 33.00 1 Tailspin Toys (Head Office) 125 9 32.00 1 Tailspin Toys (Head Office) 40 8 13.00 1 Tailspin Toys (Head Office) 28 5 13.00 1 Tailspin Toys (Head Office) 30 5 13.00 1 Tailspin Toys (Head Office) 100 120 18.00 1 Tailspin Toys (Head Office) 219 40 50.00 1 Tailspin Toys (Head Office) 159 40 18.00 1 Tailspin Toys (Head Office) 187 50 0.95 1 Tailspin Toys (Head Office) 189 156 2.90 1 Tailspin Toys (Head Office) 59 8 25.00 1 Tailspin Toys (Head Office) 167 10 99.00 1 Tailspin Toys (Head Office) 39 8 13.00 1 Tailspin Toys (Head Office) 95 0 18.00 1 Tailspin Toys (Head Office) 145 96 18.00 1 Tailspin Toys (Head Office) 194 216 4.10 1 Tailspin Toys (Head Office) 157 80 30.00 1 Tailspin Toys (Head Office) 217 30 25.00 1 Tailspin Toys (Head Office) 107 6 25.00 1 Tailspin Toys (Head Office) 213 9 87.00 1 Tailspin Toys (Head Office) 146 48 18.00 1 Tailspin Toys (Head Office) 156 40 15.00 1 Tailspin Toys (Head Office) 107 6 25.00 1 Tailspin Toys (Head Office) 196 192 4.10 1 Tailspin Toys (Head Office) 173 90 105.00 1 Tailspin Toys (Head Office) 96 84 18.00 1 Tailspin Toys (Head Office) 193 24 3.70 1 Tailspin Toys (Head Office) 177 225 1.05 1 Tailspin Toys (Head Office) 66 9 45.00 1 Tailspin Toys (Head Office) 107 6 25.00 1 Tailspin Toys (Head Office) 119 5 32.00 1 Tailspin Toys (Head Office) 115 10 34.00 1 Tailspin Toys (Head Office) 10 6 32.00 1 Tailspin Toys (Head Office) 128 1 32.00 1 Tailspin Toys (Head Office) 126 2 32.00 1 Tailspin Toys (Head Office) 94 96 18.00 1 Tailspin Toys (Head Office) 93 60 18.00 1 Tailspin Toys (Head Office) 45 1 13.00 1 Tailspin Toys (Head Office) 167 100 99.00 1 Tailspin Toys (Head Office) 44 9 13.00 1 Tailspin Toys (Head Office) 61 7 25.00 1 Tailspin Toys (Head Office) 87 84 18.00 1 Tailspin Toys (Head Office) 29 6 13.00 1 Tailspin Toys (Head Office) 183 200 2.74 1 Tailspin Toys (Head Office) 178 125 2.55 1 Tailspin Toys (Head Office) 119 4 32.00 1 Tailspin Toys (Head Office) 138 120 5.00 1 Tailspin Toys (Head Office) 160 10 33.00 1 Tailspin Toys (Head Office) 29 10 13.00 1 Tailspin Toys (Head Office) 118 9 32.00 1 Tailspin Toys (Head Office) 138 96 5.00 1 Tailspin Toys (Head Office) 147 48 18.00 1 Tailspin Toys (Head Office) 146 36 18.00 1 Tailspin Toys (Head Office) 153 30 4.50 1 Tailspin Toys (Head Office) 34 2 13.00 1 Tailspin Toys (Head Office) 46 5 13.00 1 Tailspin Toys (Head Office) 79 60 18.00 1 Tailspin Toys (Head Office) 53 5 13.00 1 Tailspin Toys (Head Office) 197 144 3.70 1 Tailspin Toys (Head Office) 134 6 32.00 1 Tailspin Toys (Head Office) 25 8 13.00 1 Tailspin Toys (Head Office) 208 84 2.70 1 Tailspin Toys (Head Office) 92 36 18.00 1 Tailspin Toys (Head Office) 22 3 13.00 1 Tailspin Toys (Head Office) 120 7 32.00 1 Tailspin Toys (Head Office) 106 1 35.00 1 Tailspin Toys (Head Office) 118 8 32.00 1 Tailspin Toys (Head Office) 195 48 3.70 1 Tailspin Toys (Head Office) 33 4 13.00 1 Tailspin Toys (Head Office) 72 5 230.00 1 Tailspin Toys (Head Office) 63 4 25.00 1 Tailspin Toys (Head Offi

# Proposition 7: Salespeople's Line Profits Over The Years

Create a view called `Sales.YearlyInvoiceLineProfits` that summarizes the total line profits from invoices for each salesperson on a yearly basis. This view allows users to analyze the profitability of each salesperson across different years. Additionally, write a query that retrieves the total line profits for each salesperson, along with a running total of profits up to each year.

### Key Objectives:

1. **Aggregate Yearly Profits**: The view aggregates line profits from invoice lines for each salesperson by year, allowing for an annual analysis of profitability.
2. **Calculate Running Totals**: The subsequent query calculates a running total of profits for each salesperson, providing insight into their cumulative performance over the years.
3. **Facilitate Reporting**: This setup facilitates reporting and analysis of salesperson performance across different time periods.

## Functional Specification

### Inputs

- **Sales.Invoices Table**: Contains invoice records, including `InvoiceID` and `InvoiceDate`.
- **Sales.InvoiceLines Table**: Contains individual line items for each invoice, including `LineProfit` and `InvoiceID`.
- **Application.People Table**: Contains records of people (salespersons), including `PersonID`, `FullName`, and a flag indicating if they are a salesperson (`IsSalesperson`).

### Outputs

- **YearOfProfit**: The year in which the profits were generated.
- **PersonID**: The unique identifier for the salesperson.
- **FullName**: The full name of the salesperson.
- **TotalLineProfit**: The total profit from invoice lines for the salesperson in that year.
- **RunningTotalProfit**: The cumulative total line profit for each salesperson up to and including the specified year.

### View Definition

The view is defined with the following components:

#### View: `Sales.YearlyInvoiceLineProfits`

- **SELECT Statement**:
    - Retrieves the year of the invoice, salesperson ID, salesperson full name, and the total line profit.
- **JOIN Operations**:
    - Joins the `Sales.Invoices` and `Sales.InvoiceLines` tables to calculate profits and further joins the `Application.People` table to filter only salespersons.
- **GROUP BY Clause**:
    - Groups results by year, salesperson ID, and full name to aggregate profits accurately.

### Query Breakdown

1. **SELECT Statement**:
    
    - Retrieves the year, salesperson ID, full name, and total line profit from the view, along with the running total profit calculated in a subquery.
2. **Running Total Subquery**:
    
    - The subquery calculates the running total by summing the total line profits for the same salesperson up to the current year.
3. **GROUP BY Clause**:
    
    - Groups the results by `PersonID`, `FullName`, `YearOfProfit`, and `TotalLineProfit`.
4. **ORDER BY Clause**:
    
    - Orders the final results by `PersonID`, `FullName`, and `YearOfProfit` for better readability.

### Assumptions

- **Data Integrity**: The `Sales.Invoices`, `Sales.InvoiceLines`, and `Application.People` tables contain valid and complete data regarding salespersons and their respective invoices and line profits.
- **Performance**: The underlying tables are properly indexed to support efficient querying, especially for large datasets.

### Edge Cases

- **No Salespersons**: If there are no salespersons marked as such (`IsSalesperson = 1`), the view will return no results.
- **No Invoices**: If no invoices exist for the specified time range, the view will return no results.

In [7]:
CREATE OR ALTER VIEW Sales.YearlyInvoiceLineProfits
AS
SELECT
    YEAR(I.InvoiceDate) AS YearOfProfit
,   P.PersonID
,   P.FullName
,   SUM(IL.LineProfit) AS TotalLineProfit
FROM Sales.Invoices AS I
    INNER JOIN Sales.InvoiceLines AS IL
        ON I.InvoiceID = IL.InvoiceID
    INNER JOIN Application.People AS P
        ON I.SalespersonPersonID = P.PersonID
            AND P.IsSalesperson = 1
GROUP BY 
    YEAR(I.InvoiceDate)
,   P.PersonID
,   P.FullName;
GO

SELECT
    YearOfProfit
,   PersonID
,   FullName
,   TotalLineProfit
,   (SELECT SUM(YILP2.TotalLineProfit)
     FROM Sales.YearlyInvoiceLineProfits AS YILP2
     WHERE YILP2.PersonID = YILP1.PersonID
        AND YILP2.YearOfProfit <= YILP1.YearOfProfit) AS RunningTotalProfit
FROM Sales.YearlyInvoiceLineProfits AS YILP1
GROUP BY 
    PersonID
,   FullName
,   YearOfProfit
,   TotalLineProfit
ORDER BY
    PersonID
,   FullName
,   YearOfProfit;

Commands completed successfully.

(40 rows affected)

Total execution time: 00:00:02.144

YearOfProfit PersonID FullName TotalLineProfit RunningTotalProfit 2013 2 Kayla Woodcock 2324243.35 2324243.35 2014 2 Kayla Woodcock 2618094.75 4942338.10 2015 2 Kayla Woodcock 2685839.30 7628177.40 2016 2 Kayla Woodcock 1100791.90 8728969.30 2013 3 Hudson Onslow 2454809.35 2454809.35 2014 3 Hudson Onslow 2407687.30 4862496.65 2015 3 Hudson Onslow 2725900.95 7588397.60 2016 3 Hudson Onslow 1083945.05 8672342.65 2013 6 Sophia Hinton 2296895.05 2296895.05 2014 6 Sophia Hinton 2503216.80 4800111.85 2015 6 Sophia Hinton 2652419.55 7452531.40 2016 6 Sophia Hinton 1084290.10 8536821.50 2013 7 Amy Trefl 2273225.20 2273225.20 2014 7 Amy Trefl 2412297.80 4685523.00 2015 7 Amy Trefl 2566381.15 7251904.15 2016 7 Amy Trefl 1091219.75 8343123.90 2013 8 Anthony Grosse 2241428.10 2241428.10 2014 8 Anthony Grosse 2402966.90 4644395.00 2015 8 Anthony Grosse 2587748.65 7232143.65 2016 8 Anthony Grosse 1063717.10 8295860.75 2013 13 Hudson Hollinworth 2144474.75 2144474.75 2014 13 Hudson Hollinworth 2545078.65 4689553.40 2015 13 Hudson Hollinworth 2721437.70 7410991.10 2016 13 Hudson Hollinworth 1137740.40 8548731.50 2013 14 Lily Code 2175934.60 2175934.60 2014 14 Lily Code 2456562.35 4632496.95 2015 14 Lily Code 2824305.20 7456802.15 2016 14 Lily Code 1073171.55 8529973.70 2013 15 Taj Shand 2238579.85 2238579.85 2014 15 Taj Shand 2512596.60 4751176.45 2015 15 Taj Shand 2627795.25 7378971.70 2016 15 Taj Shand 1234530.90 8613502.60 2013 16 Archer Lamble 2317477.15 2317477.15 2014 16 Archer Lamble 2659235.10 4976712.25 2015 16 Archer Lamble 2771563.25 7748275.50 2016 16 Archer Lamble 1205826.05 8954101.55 2013 20 Jack Potter 2301284.85 2301284.85 2014 20 Jack Potter 2310726.20 4612011.05 2015 20 Jack Potter 2794209.65 7406220.70 2016 20 Jack Potter 1099532.75 8505753.45

# Proposition 8: Double-Wide Table Of Customers Of Cs
 Identify all customers whose names start with the letter "C" and assign a row number to each customer based on the alphabetical order of `CustomerName`. Then select customers based on whether their row number has the same parity (even or odd) as the first customer whose name starts with "C". Additionally, for each selected customer, retrieve the details (ID, name, and row number) of the next customer whose name also starts with "C".
### Key Objectives:
1. **Assign Row Numbers to Customers**: The query creates a sequential `RowNum` for each customer based on the alphabetical order of `CustomerName`.
2. **Find the First "C" Customer**: It identifies the first customer whose name starts with "C" and records their row number.
3. **Select Customers Based on Row Number Parity**: The query selects customers whose row numbers have the same parity (even or odd) as the first "C" customer.
4. **Retrieve Next Customer Information**: For each selected customer, the query retrieves the `CustomerID`, `CustomerName`, and `RowNum` of the next customer in the sequence whose name starts with "C".
## Functional Specification
### Inputs
- **Sales.Customers table**: Contains customer records, including `CustomerID` and `CustomerName`.
### Outputs
- **CustomerID**: The ID of the customer whose name starts with "C".
- **CustomerName**: The name of the customer.
- **RowNum**: The row number of the customer based on alphabetical ordering.
- **NextCustomerID**: The `CustomerID` of the next customer in the sequence whose name also starts with "C".
- **NextCustomerName**: The `CustomerName` of the next customer whose name starts with "C".
- **NextRowNum**: The `RowNum` of the next customer whose name starts with "C".
### Query Breakdown
1. **Generate Row Numbers (`CustRN`)**:
    - The `ROW_NUMBER()` function assigns a sequential number (`RowNum`) to each customer ordered by `CustomerName`. The result is stored in the Common Table Expression (CTE) `CustRN`.
2. **Find First "C" Customer (`CustFirstC`)**:
    - The second CTE `CustFirstC` finds the minimum row number (`FirstRowNum`) where the `CustomerName` starts with "C".
3. **Main Query**:
- The main query retrieves customers whose names start with "C" and filters them based on whether their row number has the same parity (even or odd) as the first "C" customer.
- For each selected customer, it performs three correlated subqueries to find the next customer (with `RowNum + 1`) whose name also starts with "C", retrieving their `CustomerID`, `CustomerName`, and `RowNum`.
### Logic and Operations
1. **CTE `CustRN`**:
    
    - Generates the row number (`RowNum`) for each customer sorted by `CustomerName`.
2. **CTE `CustFirstC`**:
    
    - Finds the `FirstRowNum` for the first customer whose `CustomerName` starts with "C".
3. **Main Query**:
    
    - Filters customers whose `CustomerName` starts with "C".
    - Selects customers whose `RowNum` matches the parity of the `FirstRowNum` using modulo operation (`RowNum % 2`).
    - Correlated subqueries retrieve the details (ID, name, row number) of the next customer with the same "C" condition.
### Edge Cases
- **No Next Customer**: If no next customer exists whose name starts with "C", the subqueries will return `NULL` for `NextCustomerID`, `NextCustomerName`, and `NextRowNum`.
- **Only One "C" Customer**: If only one customer matches the "C" condition, the query will return that customer but `NULL` for the "next" customer details.
### Assumptions
- There is a significant number of customers whose names start with "C" to demonstrate the query’s functionality.
- The `Sales.Customers` table contains unique `CustomerID` and non-null `CustomerName` values.

In [8]:
WITH CustRN AS
(
    SELECT 
        CustomerID
    ,   CustomerName
    ,   ROW_NUMBER() OVER(ORDER BY CustomerName) AS RowNum
    FROM Sales.Customers
)
, CustFirstC AS
(
    SELECT MIN(RowNum) AS FirstRowNum
    FROM CustRN
    WHERE CustomerName LIKE N'C%'
)
SELECT 
    CustomerID
,   CustomerName
,   RowNum
,   (SELECT CustomerID
     FROM CustRN AS C2
     WHERE C2.RowNum = C1.RowNum + 1
        AND CustomerName LIKE N'C%') AS NextCustomerID
,   (SELECT CustomerName
     FROM CustRN AS C2
     WHERE C2.RowNum = C1.RowNum + 1
        AND CustomerName LIKE N'C%') AS NextCustomerName
,   (SELECT RowNum
     FROM CustRN AS C2
     WHERE C2.RowNum = C1.RowNum + 1
        AND CustomerName LIKE N'C%') AS NextRowNum
FROM CustRN AS C1, CustFirstC
WHERE CustomerName LIKE N'C%'
    AND RowNum % 2 =
    CASE FirstRowNum % 2
        WHEN 0 THEN 0
        ELSE 1
    END;

(8 rows affected)

Total execution time: 00:00:00.009

CustomerID CustomerName RowNum NextCustomerID NextCustomerName NextRowNum 841 Camille Authier 49 925 Can ozcan 50 853 Caterina Pinto 51 812 Celica Barajas 52 942 Chaayaadaevi Sonti 53 914 Chandana Shasthri 54 885 Chandrashekhar Dasgupta 55 899 Chin-Sun Chang 56 1030 Chompoo Atitarn 57 1046 Christian Couet 58 952 Chuan Wattanasin 59 857 Clarissa Manfrin 60 834 Cong Hoa 61 802 Cosmina Vlad 62 827 Crina Grasu 63 1033 Cuneyt Arslan 64

# Proposition 9: Leap Day Profits
Calculate the total sales amount for all orders placed on February 29th (Leap Day) during leap years, using data from the `Sales.Orders` and `Sales.OrderLines` tables. Identify orders placed specifically on February 29th of those leap years, and then sum the product of quantity and unit price from the corresponding order lines to determine the total payments made on Leap Day.
### Key Objectives:
1. **Identify Leap Years**: Extract the distinct leap years from the `Sales.Orders` table, where a leap year is defined as any year divisible by 4.
2. **Filter Orders on Leap Day**: Filter the orders that were placed specifically on February 29th in the identified leap years.
3. **Calculate Total Payments**: Calculate the total amount paid by summing the product of `Quantity` and `UnitPrice` for all orders placed on February 29th of the leap years.
## Functional Specification
### Inputs
- **Sales.Orders table**: Contains order records with attributes such as `OrderID` and `OrderDate`.
- **Sales.OrderLines table**: Contains the order line details associated with each order, including the quantity (`Quantity`) of items ordered and the price per unit (`UnitPrice`).
### Outputs
- **LeapDayPayments**: The total sum of payments made on February 29th in leap years, calculated by multiplying the quantity of each item in an order by its unit price and summing the results.
### Query Breakdown
1. **Leap Year Identification (CTE)**:
    
    - The Common Table Expression (CTE) `LeapYears` identifies the distinct leap years from the `Sales.Orders` table, where the year is divisible by 4 (`YEAR(OrderDate) % 4 = 0`).
    - Only distinct years are selected to avoid duplicates.
2. **Leap Day Filtering**:
    
    - The main query joins the `Sales.Orders` and `Sales.OrderLines` tables by matching the `OrderID`.
    - The `OrderDate` is then filtered to match February 29th (`DATEFROMPARTS(LY.LeapYear, 2, 29)`), ensuring that only orders placed on Leap Day are included.
3. **Calculate Total Leap Day Payments**:
    
    - The total payments for Leap Day are calculated by summing the product of `Quantity` and `UnitPrice` for all qualifying orders (`SUM(OL.Quantity * OL.UnitPrice)`).
4. **JOINs and WHERE Clause**:
    
- An implicit join between the CTE `LeapYears` and the `Sales.Orders` table is used to link the leap years with their corresponding orders.
- An inner join between `Sales.Orders` and `Sales.OrderLines` ensures that only orders with associated line items are considered.
### Edge Cases
- **No Orders on Leap Day**: If no orders were placed on February 29th in a given leap year, the result will be `NULL` or `0` depending on database settings.
- **Leap Years Without February 29th Orders**: Some leap years may not have any orders placed on Leap Day, and these years will not affect the result.
### Assumptions
- Leap years are correctly defined as years divisible by 4 (ignoring century and millennium rules for simplicity).
- The `Sales.Orders` and `Sales.OrderLines` tables are properly indexed, especially on `OrderDate` and `OrderID`, to ensure the query's efficiency.
- The business requirement is to sum payments for February 29th orders only in leap years.

In [9]:
WITH LeapYears AS
(
    SELECT DISTINCT YEAR(OrderDate) AS LeapYear
    FROM Sales.Orders
    WHERE YEAR(OrderDate) % 4 = 0
)
SELECT SUM(OL.Quantity * OL.UnitPrice) AS LeapDayPayments
FROM LeapYears AS LY
    ,Sales.Orders AS O
        INNER JOIN Sales.OrderLines AS OL
            ON O.OrderID = OL.OrderID
WHERE OrderDate = DATEFROMPARTS(LY.LeapYear, 2, 29);


(1 row affected)

Total execution time: 00:00:00.031

LeapDayPayments 278101.45

# Proposition 10: Customer's Top Most Recent Items Purchased
Create a user-defined table-valued function (`Sales.CustRecentOrders`) that retrieves the most recent `n` orders for a specific customer, along with the total quantity of each item ordered. Use this function in an `OUTER APPLY` query to return a list of recent orders for all customers, including the date of the order, the name of the item, and the total quantity ordered.
### Key Objectives:
1. **Function Creation**: Create or modify a function (`Sales.CustRecentOrders`) that returns the top `n` recent orders for a given customer, including the total quantity of each item ordered.
2. **Usage of the Function**: The function is utilized with the `OUTER APPLY` clause to display the recent orders of each customer from the `Sales.Customers` table.
3. **Display Recent Orders**: The query displays customer name, order date, item name, and total quantity ordered for the three most recent orders of each customer.
## Functional Specification
### Inputs
- **Sales.CustRecentOrders function**:
    - `@custid`: The ID of the customer for whom the recent orders are fetched.
    - `@n`: The number of most recent orders to return.
- **Tables**:
    - **Sales.Orders**: Contains information on customer orders (`OrderID`, `CustomerID`, and `OrderDate`).
    - **Sales.OrderLines**: Contains details of items ordered (`OrderID`, `StockItemID`, and `Quantity`).
    - **Warehouse.StockItems**: Contains stock item information (`StockItemID` and `StockItemName`).
    - **Sales.Customers**: Contains customer information (`CustomerID` and `CustomerName`).
### Outputs
- **CustomerName**: The name of the customer who placed the order.
- **OrderDate**: The date of the order.
- **StockItemName**: The name of the stock item ordered.
- **TotalQuantity**: The total quantity of the stock item ordered in that order.
### Function Breakdown: `Sales.CustRecentOrders`
1. **Parameters**:
    
    - The function accepts a `CustomerID` (`@custid`) and a number `n` (`@n`) to return the top `n` recent orders for that customer.
2. **Joins**:
    
    - The function joins the `Sales.Orders` table with the `Sales.OrderLines` table to get the quantities of each item ordered.
    - The function further joins the `Warehouse.StockItems` table to retrieve the names of the stock items ordered.
3. **Data Aggregation**:
    
    - The function groups the results by `StockItemName` and `OrderDate` to get the total quantity ordered per stock item for each order.
4. **Ordering**:
    
    - The results are ordered by `OrderDate` in descending order (most recent first), and by `TotalQuantity` in descending order within each order date.
5. **Return**:
    
    - The function returns the top `n` recent orders as a table.
### Query Breakdown: Customer Orders
1. **OUTER APPLY**:
    
    - The `OUTER APPLY` operator is used to call the `Sales.CustRecentOrders` function for each customer in the `Sales.Customers` table. It retrieves the three most recent orders for each customer (`C.CustomerID`) by passing `3` as the value of `@n`.
2. **Columns**:
    
    - The query selects the `CustomerName`, the order date (`OrderDate`), the name of the stock item (`StockItemName`), and the total quantity ordered (`TotalQuantity`) for each customer's recent orders.
3. **Handling Customers with No Orders**:
    
- Since `OUTER APPLY` is used, customers who have no recent orders will still be included in the result set with `NULL` values for order-related fields.
### Edge Cases
- **Customers with No Orders**: If a customer has no orders, the query will return `NULL` values for `OrderDate`, `StockItemName`, and `TotalQuantity`.
- **Ties in Quantity**: If two items in the same order have the same `TotalQuantity`, both will be included in the result set, as no tie-breaking rule for stock items is specified.
### Assumptions
- The `Sales.Orders`, `Sales.OrderLines`, `Warehouse.StockItems`, and `Sales.Customers` tables are properly indexed, especially on `CustomerID`, `OrderDate`, `OrderID`, and `StockItemID` for optimal performance.
- The requirement is to retrieve only the top 3 most recent orders per customer.

In [10]:
CREATE OR ALTER FUNCTION Sales.CustRecentOrders
    (@custid AS INT, @n AS INT) RETURNS TABLE
AS
RETURN
    SELECT TOP (@n) O.OrderDate, SI.StockItemName, SUM(OL.Quantity) AS TotalQuantity
    FROM Sales.Orders AS O
        INNER JOIN Sales.OrderLines AS OL
            ON O.OrderID = OL.OrderID
        INNER JOIN Warehouse.StockItems AS SI
            ON OL.StockItemID = SI.StockItemID
    WHERE O.CustomerID = @custid
    GROUP BY SI.StockItemName, O.OrderDate
    ORDER BY O.OrderDate DESC, TotalQuantity DESC
GO

SELECT C.CustomerName, CRO.OrderDate, CRO.StockItemName, CRO.TotalQuantity
FROM Sales.Customers AS C
    OUTER APPLY Sales.CustRecentOrders(C.CustomerID, 3) AS CRO;


Commands completed successfully.

(1989 rows affected)

Total execution time: 00:00:01.135

CustomerName OrderDate StockItemName TotalQuantity Tailspin Toys (Head Office) 2016-05-27 Tape dispenser (Black) 50 Tailspin Toys (Head Office) 2016-05-27 10 mm Double sided bubble wrap 20m 20 Tailspin Toys (Head Office) 2016-04-28 RC big wheel monster truck with remote control (Black) 1/50 scale 9 Tailspin Toys (Sylvanite, MT) 2016-05-14 Halloween skull mask (Gray) S 84 Tailspin Toys (Sylvanite, MT) 2016-05-14 DBA joke mug - daaaaaa-ta (White) 1 Tailspin Toys (Sylvanite, MT) 2016-05-12 Office cube periscope (Black) 90 Tailspin Toys (Peeples Valley, AZ) 2016-05-30 "The Gu" red shirt XML tag t-shirt (White) S 120 Tailspin Toys (Peeples Valley, AZ) 2016-05-30 20 mm Anti static bubble wrap (Blue) 50m 90 Tailspin Toys (Peeples Valley, AZ) 2016-05-19 Clear packaging tape 48mmx75m 234 Tailspin Toys (Medicine Lodge, KS) 2016-04-28 "The Gu" red shirt XML tag t-shirt (Black) 6XL 60 Tailspin Toys (Medicine Lodge, KS) 2016-04-28 DBA joke mug - it depends (White) 7 Tailspin Toys (Medicine Lodge, KS) 2016-04-28 Developer joke mug - understanding recursion requires understanding recursion (White) 1 Tailspin Toys (Gasport, NY) 2016-05-28 Alien officer hoodie (Black) 4XL 8 Tailspin Toys (Gasport, NY) 2016-05-28 Developer joke mug - inheritance is the OO way to become wealthy (Black) 7 Tailspin Toys (Gasport, NY) 2016-05-28 Developer joke mug - this code was generated by a tool (White) 5 Tailspin Toys (Jessie, ND) 2016-05-31 Void fill 100 L bag (White) 100L 80 Tailspin Toys (Jessie, ND) 2016-05-31 Black and orange handle with care despatch tape 48mmx75m 48 Tailspin Toys (Jessie, ND) 2016-05-31 Plush shark slippers (Gray) L 7 Tailspin Toys (Frankewing, TN) 2016-05-27 "The Gu" red shirt XML tag t-shirt (White) XS 48 Tailspin Toys (Frankewing, TN) 2016-05-27 Void fill 400 L bag (White) 400L 10 Tailspin Toys (Frankewing, TN) 2016-05-27 USB food flash drive - sushi roll 4 Tailspin Toys (Bow Mar, CO) 2016-05-20 Red and white urgent heavy despatch tape 48mmx100m 120 Tailspin Toys (Bow Mar, CO) 2016-05-20 Black and yellow heavy despatch tape 48mmx100m 48 Tailspin Toys (Bow Mar, CO) 2016-05-20 USB food flash drive - shrimp cocktail 9 Tailspin Toys (Netcong, NJ) 2016-05-24 Shipping carton (Brown) 480x270x320mm 225 Tailspin Toys (Netcong, NJ) 2016-05-24 Developer joke mug - when your hammer is C++ (White) 1 Tailspin Toys (Netcong, NJ) 2016-05-17 "The Gu" red shirt XML tag t-shirt (Black) XS 108 Tailspin Toys (Wimbledon, ND) 2016-05-24 IT joke mug - that behavior is by design (White) 10 Tailspin Toys (Wimbledon, ND) 2016-05-24 Pack of 12 action figures (female) 7 Tailspin Toys (Wimbledon, ND) 2016-05-11 Black and orange glass with care despatch tape 48mmx100m 24 Tailspin Toys (Devault, PA) 2016-05-31 "The Gu" red shirt XML tag t-shirt (White) M 120 Tailspin Toys (Devault, PA) 2016-05-31 Red and white urgent despatch tape 48mmx75m 72 Tailspin Toys (Devault, PA) 2016-05-31 Superhero action jacket (Blue) M 10 Tailspin Toys (Biscay, MN) 2016-05-27 Black and orange this way up despatch tape 48mmx100m 120 Tailspin Toys (Biscay, MN) 2016-05-27 Black and orange this way up despatch tape 48mmx75m 72 Tailspin Toys (Biscay, MN) 2016-05-27 "The Gu" red shirt XML tag t-shirt (White) L 12 Tailspin Toys (Stonefort, IL) 2016-05-26 Shipping carton (Brown) 279x254x217mm 175 Tailspin Toys (Stonefort, IL) 2016-05-26 Shipping carton (Brown) 480x270x320mm 150 Tailspin Toys (Stonefort, IL) 2016-05-26 White chocolate snow balls 250g 96 Tailspin Toys (Long Meadow, MD) 2016-05-30 Shipping carton (Brown) 305x305x305mm 150 Tailspin Toys (Long Meadow, MD) 2016-05-30 10 mm Anti static bubble wrap (Blue) 50m 80 Tailspin Toys (Long Meadow, MD) 2016-05-30 Chocolate sharks 250g 24 Tailspin Toys (Batson, TX) 2016-04-13 Furry animal socks (Pink) S 72 Tailspin Toys (Batson, TX) 2016-04-13 Developer joke mug - old C developers never die (White) 8 Tailspin Toys (Batson, TX) 2016-04-13 DBA joke mug - I will get you in order (Black) 3 Tailspin Toys (Coney Island, MO) 2016-05-27 Void fill 300 L b